In [1]:
import numpy as np

In [2]:
def isSymmetric(A):
    #gibt zurück, ob die Matrix A symmetrisch ist
    n=len(A)
    if(n==0):
        print("A ist leer!")
        return False
    for i in range(n):
        if(len(A[i])!=n):
            print("A keine quadratische Matrix")
            return False
    for i in range(n):
        for j in range(i+1,n):
            if(A[i][j]!=A[j][i]):
                print("a_%s,%s =/=a_%s,%s" % (i,j,j,i))
                return False;
    return True

In [3]:
def cholesky(A):
    if(not isSymmetric(A)):
        print("A ist nicht symmetrisch")
        return None
    n=len(A)
    L=np.zeros((n,n))
    for i in range(n): #wir gehen zeilenweise die Einträge durch
        
        for j in range(i):
            #berechne Eintrag L[i][j] für 0<=j<=i-1
            sum=A[i][j]
            for k in range(j):
                sum-=L[i][k]*L[j][k]
            L[i][j]=sum/L[j][j]
        
        #berechne Eintrag L[i][i]
        sum=A[i][i]
        for k in range(i):
            sum-=L[i][k]**2
        if(sum<=0):
            print("A ist nicht positiv definit")
            return None
        L[i][i]=np.sqrt(sum)
    return L

In [4]:
A=[
[4,2,0],
[2,3,-1],
[0,-1,3]
]

In [5]:
L=cholesky(A)
print("L=   %s" %L)
print(L.dot(L.T))

L=   [[ 2.          0.          0.        ]
 [ 1.          1.41421356  0.        ]
 [ 0.         -0.70710678  1.58113883]]
[[ 4.  2.  0.]
 [ 2.  3. -1.]
 [ 0. -1.  3.]]


In [20]:
'''
Im folgenden benutzen wir die Cholesky-Zerlegung um für eine Sammlung von (pseudo)-Messwerten,
die beste Approximation für eine affine Funktion f:R^2 -> R , x -> f(x)=a+bx_1+cx_2 zu finden (s. Bsp 2.18).
'''

'\nIm folgenden benutzen wir die Cholesky-Zerlegung um für eine Sammlung von (pseudo)-Messwerten,\ndie beste Approximation für eine affine Funktion f:R^2 -> R , x -> f(x)=a+bx_1+cx_2 zu finden (s. Bsp 2.18).\n'

In [6]:
#erzeugt pseudo-Messwerte mit 0<=x1,x2<n und zufälligem Fehler mit Betrag <e

import random

def fun(x1,x2):
    return 3+2*x1-3*x2

def giveMeasurements(n,e):
    measures=[]
    for i in range(n):
        for j in range(n):
            fault=random.uniform(-e,e)
            measures.append([i,j,fun(i,j)+fault])
    return measures

In [7]:
n=3

#die erhaltenen Messungen
meas=giveMeasurements(n,0.1)
for m in meas:
    print(m)

[0, 0, 2.948685033226322]
[0, 1, 0.03893176837770984]
[0, 2, -2.903546881368285]
[1, 0, 4.923536211345981]
[1, 1, 1.9143227566707914]
[1, 2, -1.0887443597865865]
[2, 0, 7.018761972756901]
[2, 1, 3.993092173089257]
[2, 2, 1.0449216767416605]


In [8]:
#Aus grad QF(r)=0 erhalten wir das LGS Bx=b mit:

B=np.zeros((3,3))
b=np.zeros(3)

for m in meas: #summiere über die einzelnen Messungwerte. x1=m[0], x2=m[1], y=m[2]
    B[0][0]+=1
    B[0][1]+=m[0]
    B[0][2]+=m[1]
    B[1][1]+=m[0]*m[0]
    B[1][2]+=m[0]*m[1]
    B[2][2]+=m[1]**2
    b[0]+=m[2]
    b[1]+=m[0]*m[2]
    b[2]+=m[1]*m[2]
B[1][0]=B[0][1]
B[2][0]=B[0][2]
B[2][1]=B[1][2]

In [9]:
print(B) #hängt nicht von y ab, sondern nur von den Messpunkten (x_1,x_2)
print(b)

[[ 9.  9.  9.]
 [ 9. 15.  9.]
 [ 9.  9. 15.]]
[17.88996035 29.86266625  0.05160757]


In [19]:
#löse das LGS nach r auf:
L=cholesky(B)
print("Zerlegung von B ergibt die untere Dreicksmatrix L=\n %s" %L)

#Löse das LGS schrittweise auf. Hier würde wir eigentlich rückwärts/vorwärts von Blatt 5 verwenden
y=np.linalg.solve(L,b) 
r=np.linalg.solve(L.T,y)
print("\n Die Koeffizenten sind %s" %r)
print("also ist unsere Funktion f(x)=%s+%s*x1+ %s*x_2"  %(r[0],r[1],r[2]))

Zerlegung von B ergibt die untere Dreicksmatrix L=
 [[3.         0.         0.        ]
 [3.         2.44948974 0.        ]
 [3.         0.         2.44948974]]

 Die Koeffizenten sind [ 2.96538119  1.99545098 -2.9730588 ]
also ist unsere Funktion f(x)=2.9653811855710295+1.9954509837253456*x1+ -2.9730587969570696*x_2
